# Object

```{admonition} 核心功能
`Object` 是 TVM 运行时所有对象的基类，主要提供以下核心能力：
- 类型系统：通过类型索引(`type_index`)实现运行时类型识别(RTTI)
- 引用计数：管理对象生命周期
- 内存管理：通过自定义删除器控制对象销毁
```

````{admonition} 类型相关属性

```cpp
static constexpr const char* _type_key = "runtime.Object";
static constexpr uint32_t _type_index = TypeIndex::kDynamic;
```
- `_type_key`：类型唯一标识符（如 `"runtime.NDArray"`）
- `_type_index`：类型索引（`kDynamic` 表示动态分配）
````

````{admonition} 引用计数器

```cpp
#if TVM_OBJECT_ATOMIC_REF_COUNTER
  using RefCounterType = std::atomic<int32_t>;
#else
  using RefCounterType = int32_t; 
#endif
```
- 支持原子/非原子计数器选择
- 控制对象是否支持多线程共享
````

````{admonition} 类型继承控制
```cpp
static constexpr bool _type_final = false;
static constexpr uint32_t _type_child_slots = 0;
static constexpr bool _type_child_slots_can_overflow = true;
```
- `_type_final`：是否允许继承
- `_type_child_slots`：为子类预留的类型槽位
- `_type_child_slots_can_overflow`：是否允许超量子类数量
````

使用示例：
```cpp
// 创建对象示例
class MyObject : public Object {
 public:
  int my_data;
  
  static constexpr const char* _type_key = "custom.MyObject";
  TVM_DECLARE_FINAL_OBJECT_INFO(MyObject, Object);
};

// 注册类型（需在.cc文件中）
TVM_REGISTER_OBJECT_TYPE(MyObject);

// 使用示例
ObjectRef obj_ref = make_object<MyObject>();
const MyObject* ptr = obj_ref.as<MyObject>();
```

```{admonition} 设计亮点 
1. 高效类型检查：通过预分配的 `type_index` 实现 O(1) 时间复杂度类型判断 
2. 灵活继承：通过 `_type_child_slots` 在类型安全与性能之间取得平衡 
3. 线程安全：可配置的原子计数器支持多线程场景 
4. 内存控制：自定义删除器支持特殊内存分配策略  

该设计为 TVM 的异构计算场景提供了高效的对象管理基础，特别是在需要频繁跨语言边界传递对象时（如 Python/C++ 交互），能保证类型安全和内存安全。
```